# ANALYZING THE PERPLEXITY OF MERAK-7B-V1 USING MBZUAI/BACTRIAN-X DATASET

### WARNING = This notebook needs HUGE VRAM for successfully run it. It needs at least 48 GB of VRAM

Let's Install the packages requirement.

In [1]:
!pip install bitsandbytes==0.39.1
!pip install transformers==4.31.0
!pip install peft==0.4.0
!pip install accelerate==0.20.3
!pip install einops==0.6.1 scipy sentencepiece datasets

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 97.1/97.1 MB 41.5 MB/s eta 0:00:0000:0100:01

[notice] A new release of pip is available: 23.0.1 -> 23.2.1
[notice] To update, run: python -m pip install --upgrade pip
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.4/7.4 MB 90.5 MB/s eta 0:00:00:00:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 51.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 95.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 95.4 MB/s eta 0:00:00:00:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.1/77.1 kB 42.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 770.4/770.4 kB 104.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 163.8/163.8 kB 71.4 MB/s eta 0:00:00

[notice] A new release of pip is available: 23.0.1 -> 23.2.1
[notice] To update, run: python -m pip install --upgrade pip
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 72.9/72.9 kB 20.8 MB/s eta 0:00:00

In [2]:
import torch
import pandas as pd
import numpy as np

In [3]:
from transformers import AutoModelForCausalLM, LlamaTokenizer, BitsAndBytesConfig

BNB_CONFIG = BitsAndBytesConfig(load_in_4bit=True,
                                bnb_4bit_compute_dtype=torch.bfloat16,
                                bnb_4bit_use_double_quant=True,
                                bnb_4bit_quant_type="nf4",
    )

model = AutoModelForCausalLM.from_pretrained("Ichsan2895/Merak-7B-v1",
                                             quantization_config=BNB_CONFIG,
                                             device_map="auto")
tokenizer = LlamaTokenizer.from_pretrained("Ichsan2895/Merak-7B-v1")


===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please run

python -m bitsandbytes

 and submit this information together with your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
bin /usr/local/lib/python3.10/dist-packages/bitsandbytes/libbitsandbytes_cuda116.so
CUDA_SETUP: WARNING! libcudart.so not found in any environmental path. Searching in backup paths...
CUDA SETUP: CUDA runtime path found: /usr/local/cuda/lib64/libcudart.so
CUDA SETUP: Highest compute capability among GPUs detected: 8.6
CUDA SETUP: Detected CUDA version 116
CUDA SETUP: Loading binary /usr/local/lib/python3.10/dist-packages/bitsandbytes/libbitsandbytes_cuda116.so...


/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('/usr/local/nvidia/lib'), PosixPath('/usr/local/nvidia/lib64')}
  warn(msg)
/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: /usr/local/nvidia/lib:/usr/local/nvidia/lib64 did not contain ['libcudart.so', 'libcudart.so.11.0', 'libcudart.so.12.0'] as expected! Searching further paths...
  warn(msg)
/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('noninteractive    SHELL=/bin/bash')}
  warn(msg)
/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('module'), PosixPath('//matplotlib_inline.backend_

Loading checkpoint shards:   0%|          | 0/6 [00:00<?, ?it/s]

Intuitively, perplexity means to be surprised. We measure how much the model is surprised by seeing new data. The lower the perplexity, the better the training is (Priyanka, 2022).

In [4]:
inputs = tokenizer("Saya menyukai tari zapin", return_tensors = "pt")
loss = model(input_ids = inputs["input_ids"], labels = inputs["input_ids"]).loss
ppl = torch.exp(loss)
print(ppl)

tensor(228.6252, grad_fn=<ExpBackward0>)


### Now, we learn how to calculate perplexity in a text in Pandas Dataframe

In [5]:
df = pd.read_csv("eval_single.csv")
df

QuestionAnswer
0  <|prompt|>Siapa penulis naskah proklamasi keme...

In [6]:
def Perplexity(TEXT):
    inputs = tokenizer(TEXT, return_tensors = "pt")
    with torch.inference_mode():
        loss = model(input_ids = inputs["input_ids"], labels = inputs["input_ids"]).loss
    ppl = torch.exp(loss)
    return np.float16(ppl.detach().numpy())

In [7]:
df['PPL'] = df['QuestionAnswer'].apply(Perplexity)
df

QuestionAnswer     PPL
0  <|prompt|>Siapa penulis naskah proklamasi keme...  7.3125

It has PPL of 7.3125. It much lower than first example. So, it was better.

### LETS CALCULATE PERPLEXITY OF MERAK-7B-V1

In [8]:
from datasets import load_dataset

#### We never trained Merak-7B-v1 with MBZUAI/Bactrian-X. So, it was good dataset for evaluation how good the model is..

In [9]:
dataset_name = "MBZUAI/Bactrian-X"
dataset = load_dataset(dataset_name, "id", split="train")
dataset

Generating train split: 0 examples [00:00, ? examples/s]

Dataset({
    features: ['instruction', 'input', 'id', 'output'],
    num_rows: 67017
})

In [10]:
df_MBZUAI = pd.DataFrame( {'instruction':dataset['instruction'],
                           'input':dataset['input'],
                           'output':dataset['output']} )
df_MBZUAI

instruction  \
0      Laporkan suhu rata-rata di Scottsdale, AZ pada...   
1                     Bagaimana cara kerja turbin angin?   
2       Hasilkan daftar ras anjing paling populer di AS.   
3                Apa itu jaringan pribadi virtual (VPN)?   
4      Identifikasi tema puisi Pablo Neruda "If You F...   
...                                                  ...   
67012  Sarankan langkah kebijakan baru untuk mengatas...   
67013  Kembangkan pernyataan tesis yang menangkap ese...   
67014  Sarankan beberapa tindakan yang dapat diambil ...   
67015  Cocokkan masukan berikut dengan jenis tugas pe...   
67016  Tulis postingan mikroblog tentang pengalaman t...   

                                                   input  \
0                                                          
1                                                          
2                                                          
3                                                          
4                                                          
...                                                  ...   
67012  Ada tren kejahatan dunia maya yang berkembang ...   
67013  Artikel ini akan mengeksplorasi bagaimana berb...   
67014                                                      
67015                                      Gambar kucing   
67016                                                      

                                                  output  
0      Tidak ditemukan data suhu rata-rata untuk Scot...  
1      Turbin angin bekerja dengan mengubah energi ki...  
2      1. Labradoodle\n2. Bulldog Inggris\n3. Golden ...  
3      Jaringan pribadi virtual (VPN) adalah sebuah t...  
4      Tema puisi "If You Forget Me" karya Pablo Neru...  
...                                                  ...  
67012  1. Peningkatan Kesadaran Masyarakat. Melalui k...  
67013  Pernyataan tesis dari artikel ini adalah bahwa...  
67014  Sebagai AI, saya akan memberikan beberapa sara...  
67015       Pembelajaran mesin dalam klasifikasi gambar.  
67016  Baru saja merasakan pengalaman yang sangat men...  

[67017 rows x 3 columns]

### Since the dataset has some rows which has 'input' column, we examine that with different approach for creating QnA text 

When the data has no 'input' column, the format is:  
`<|prompt|>{instruction}<|answer|>{output}`

In [11]:
df_MBZUAI_NoInput = df_MBZUAI[df_MBZUAI['input']=='']
df_MBZUAI_NoInput

instruction input  \
0      Laporkan suhu rata-rata di Scottsdale, AZ pada...         
1                     Bagaimana cara kerja turbin angin?         
2       Hasilkan daftar ras anjing paling populer di AS.         
3                Apa itu jaringan pribadi virtual (VPN)?         
4      Identifikasi tema puisi Pablo Neruda "If You F...         
...                                                  ...   ...   
67007  Identifikasi 3 faktor yang dapat berdampak neg...         
67008                             Ciptakan olahraga baru         
67009  Kembangkan strategi untuk mengoptimalkan konte...         
67014  Sarankan beberapa tindakan yang dapat diambil ...         
67016  Tulis postingan mikroblog tentang pengalaman t...         

                                                  output  
0      Tidak ditemukan data suhu rata-rata untuk Scot...  
1      Turbin angin bekerja dengan mengubah energi ki...  
2      1. Labradoodle\n2. Bulldog Inggris\n3. Golden ...  
3      Jaringan pribadi virtual (VPN) adalah sebuah t...  
4      Tema puisi "If You Forget Me" karya Pablo Neru...  
...                                                  ...  
67007  1. Ketidakstabilan Ekonomi: Fluktuasi dalam ek...  
67008  Sebagai AI, saya tidak memiliki ide atau kreat...  
67009  1. Melakukan penelitian kata kunci: Lakukan pe...  
67014  Sebagai AI, saya akan memberikan beberapa sara...  
67016  Baru saja merasakan pengalaman yang sangat men...  

[41764 rows x 3 columns]

In [12]:
df_MBZUAI_NoInput['QnA'] = "<|prompt|>" + df_MBZUAI_NoInput["instruction"].astype(str) + "<|answer|>" + df_MBZUAI_NoInput["output"].astype(str)
df_MBZUAI_NoInput

/tmp/ipykernel_486/1761940573.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_MBZUAI_NoInput['QnA'] = "<|prompt|>" + df_MBZUAI_NoInput["instruction"].astype(str) + "<|answer|>" + df_MBZUAI_NoInput["output"].astype(str)


instruction input  \
0      Laporkan suhu rata-rata di Scottsdale, AZ pada...         
1                     Bagaimana cara kerja turbin angin?         
2       Hasilkan daftar ras anjing paling populer di AS.         
3                Apa itu jaringan pribadi virtual (VPN)?         
4      Identifikasi tema puisi Pablo Neruda "If You F...         
...                                                  ...   ...   
67007  Identifikasi 3 faktor yang dapat berdampak neg...         
67008                             Ciptakan olahraga baru         
67009  Kembangkan strategi untuk mengoptimalkan konte...         
67014  Sarankan beberapa tindakan yang dapat diambil ...         
67016  Tulis postingan mikroblog tentang pengalaman t...         

                                                  output  \
0      Tidak ditemukan data suhu rata-rata untuk Scot...   
1      Turbin angin bekerja dengan mengubah energi ki...   
2      1. Labradoodle\n2. Bulldog Inggris\n3. Golden ...   
3      Jaringan pribadi virtual (VPN) adalah sebuah t...   
4      Tema puisi "If You Forget Me" karya Pablo Neru...   
...                                                  ...   
67007  1. Ketidakstabilan Ekonomi: Fluktuasi dalam ek...   
67008  Sebagai AI, saya tidak memiliki ide atau kreat...   
67009  1. Melakukan penelitian kata kunci: Lakukan pe...   
67014  Sebagai AI, saya akan memberikan beberapa sara...   
67016  Baru saja merasakan pengalaman yang sangat men...   

                                                     QnA  
0      <|prompt|>Laporkan suhu rata-rata di Scottsdal...  
1      <|prompt|>Bagaimana cara kerja turbin angin?<|...  
2      <|prompt|>Hasilkan daftar ras anjing paling po...  
3      <|prompt|>Apa itu jaringan pribadi virtual (VP...  
4      <|prompt|>Identifikasi tema puisi Pablo Neruda...  
...                                                  ...  
67007  <|prompt|>Identifikasi 3 faktor yang dapat ber...  
67008  <|prompt|>Ciptakan olahraga baru<|answer|>Seba...  
67009  <|prompt|>Kembangkan strategi untuk mengoptima...  
67014  <|prompt|>Sarankan beberapa tindakan yang dapa...  
67016  <|prompt|>Tulis postingan mikroblog tentang pe...  

[41764 rows x 4 columns]

When the data has 'input' column, the format is:  
`<|prompt|>{instruction}: {input}<|answer|>{output}`

In [13]:
df_MBZUAI_WithInput = df_MBZUAI[df_MBZUAI['input']!='']
df_MBZUAI_WithInput

instruction  \
7      Kategorikan film ini ke dalam salah satu genre...   
9         Ubah string berikut menjadi huruf kecil penuh.   
19     Diberi string berikut 'a1b2c3', ubah menjadi '...   
20     Berikan ulasan untuk restoran dalam 200 kata a...   
22     Buat hidangan baru menggunakan bahan-bahan ber...   
...                                                  ...   
67010                 Beri judul artikel yang diberikan.   
67011  Tulis ulang cerita sehingga memiliki akhir yan...   
67012  Sarankan langkah kebijakan baru untuk mengatas...   
67013  Kembangkan pernyataan tesis yang menangkap ese...   
67015  Cocokkan masukan berikut dengan jenis tugas pe...   

                                                   input  \
7                                               Revenant   
9                                                   Halo   
19                                                a1b2c3   
20                                            Gajah Liar   
22           Wortel, bawang putih, bawang merah, brokoli   
...                                                  ...   
67010  Artikel ini akan membahas masalah mendesak def...   
67011  Alkisah, hiduplah seekor unicorn ajaib di huta...   
67012  Ada tren kejahatan dunia maya yang berkembang ...   
67013  Artikel ini akan mengeksplorasi bagaimana berb...   
67015                                      Gambar kucing   

                                                  output  
7                                                 Drama.  
9                                                   halo  
19     dapat diubah menjadi 'abc123' dengan menggunak...  
20     Restoran Gajah Liar adalah tempat yang menyaji...  
22     dapat dipadukan menjadi hidangan sehat yang le...  
...                                                  ...  
67010  "Urgensi Menangani Deforestasi: Dampaknya terh...  
67011  Tapi, kekagumannya berubah menjadi kesedihan k...  
67012  1. Peningkatan Kesadaran Masyarakat. Melalui k...  
67013  Pernyataan tesis dari artikel ini adalah bahwa...  
67015       Pembelajaran mesin dalam klasifikasi gambar.  

[25253 rows x 3 columns]

In [14]:
df_MBZUAI_WithInput['QnA'] = "<|prompt|>" + df_MBZUAI_WithInput["instruction"].astype(str) + ": " + df_MBZUAI_WithInput["input"].astype(str) + "<|answer|>" + df_MBZUAI_WithInput["output"].astype(str)
df_MBZUAI_WithInput

/tmp/ipykernel_486/3992297062.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_MBZUAI_WithInput['QnA'] = "<|prompt|>" + df_MBZUAI_WithInput["instruction"].astype(str) + ": " + df_MBZUAI_WithInput["input"].astype(str) + "<|answer|>" + df_MBZUAI_WithInput["output"].astype(str)


instruction  \
7      Kategorikan film ini ke dalam salah satu genre...   
9         Ubah string berikut menjadi huruf kecil penuh.   
19     Diberi string berikut 'a1b2c3', ubah menjadi '...   
20     Berikan ulasan untuk restoran dalam 200 kata a...   
22     Buat hidangan baru menggunakan bahan-bahan ber...   
...                                                  ...   
67010                 Beri judul artikel yang diberikan.   
67011  Tulis ulang cerita sehingga memiliki akhir yan...   
67012  Sarankan langkah kebijakan baru untuk mengatas...   
67013  Kembangkan pernyataan tesis yang menangkap ese...   
67015  Cocokkan masukan berikut dengan jenis tugas pe...   

                                                   input  \
7                                               Revenant   
9                                                   Halo   
19                                                a1b2c3   
20                                            Gajah Liar   
22           Wortel, bawang putih, bawang merah, brokoli   
...                                                  ...   
67010  Artikel ini akan membahas masalah mendesak def...   
67011  Alkisah, hiduplah seekor unicorn ajaib di huta...   
67012  Ada tren kejahatan dunia maya yang berkembang ...   
67013  Artikel ini akan mengeksplorasi bagaimana berb...   
67015                                      Gambar kucing   

                                                  output  \
7                                                 Drama.   
9                                                   halo   
19     dapat diubah menjadi 'abc123' dengan menggunak...   
20     Restoran Gajah Liar adalah tempat yang menyaji...   
22     dapat dipadukan menjadi hidangan sehat yang le...   
...                                                  ...   
67010  "Urgensi Menangani Deforestasi: Dampaknya terh...   
67011  Tapi, kekagumannya berubah menjadi kesedihan k...   
67012  1. Peningkatan Kesadaran Masyarakat. Melalui k...   
67013  Pernyataan tesis dari artikel ini adalah bahwa...   
67015       Pembelajaran mesin dalam klasifikasi gambar.   

                                                     QnA  
7      <|prompt|>Kategorikan film ini ke dalam salah ...  
9      <|prompt|>Ubah string berikut menjadi huruf ke...  
19     <|prompt|>Diberi string berikut 'a1b2c3', ubah...  
20     <|prompt|>Berikan ulasan untuk restoran dalam ...  
22     <|prompt|>Buat hidangan baru menggunakan bahan...  
...                                                  ...  
67010  <|prompt|>Beri judul artikel yang diberikan.: ...  
67011  <|prompt|>Tulis ulang cerita sehingga memiliki...  
67012  <|prompt|>Sarankan langkah kebijakan baru untu...  
67013  <|prompt|>Kembangkan pernyataan tesis yang men...  
67015  <|prompt|>Cocokkan masukan berikut dengan jeni...  

[25253 rows x 4 columns]

Now combine the 2 datasets into one dataframe using pandas concat

In [15]:
df_MBZUAI = pd.concat([df_MBZUAI_NoInput,df_MBZUAI_WithInput])
df_MBZUAI

instruction  \
0      Laporkan suhu rata-rata di Scottsdale, AZ pada...   
1                     Bagaimana cara kerja turbin angin?   
2       Hasilkan daftar ras anjing paling populer di AS.   
3                Apa itu jaringan pribadi virtual (VPN)?   
4      Identifikasi tema puisi Pablo Neruda "If You F...   
...                                                  ...   
67010                 Beri judul artikel yang diberikan.   
67011  Tulis ulang cerita sehingga memiliki akhir yan...   
67012  Sarankan langkah kebijakan baru untuk mengatas...   
67013  Kembangkan pernyataan tesis yang menangkap ese...   
67015  Cocokkan masukan berikut dengan jenis tugas pe...   

                                                   input  \
0                                                          
1                                                          
2                                                          
3                                                          
4                                                          
...                                                  ...   
67010  Artikel ini akan membahas masalah mendesak def...   
67011  Alkisah, hiduplah seekor unicorn ajaib di huta...   
67012  Ada tren kejahatan dunia maya yang berkembang ...   
67013  Artikel ini akan mengeksplorasi bagaimana berb...   
67015                                      Gambar kucing   

                                                  output  \
0      Tidak ditemukan data suhu rata-rata untuk Scot...   
1      Turbin angin bekerja dengan mengubah energi ki...   
2      1. Labradoodle\n2. Bulldog Inggris\n3. Golden ...   
3      Jaringan pribadi virtual (VPN) adalah sebuah t...   
4      Tema puisi "If You Forget Me" karya Pablo Neru...   
...                                                  ...   
67010  "Urgensi Menangani Deforestasi: Dampaknya terh...   
67011  Tapi, kekagumannya berubah menjadi kesedihan k...   
67012  1. Peningkatan Kesadaran Masyarakat. Melalui k...   
67013  Pernyataan tesis dari artikel ini adalah bahwa...   
67015       Pembelajaran mesin dalam klasifikasi gambar.   

                                                     QnA  
0      <|prompt|>Laporkan suhu rata-rata di Scottsdal...  
1      <|prompt|>Bagaimana cara kerja turbin angin?<|...  
2      <|prompt|>Hasilkan daftar ras anjing paling po...  
3      <|prompt|>Apa itu jaringan pribadi virtual (VP...  
4      <|prompt|>Identifikasi tema puisi Pablo Neruda...  
...                                                  ...  
67010  <|prompt|>Beri judul artikel yang diberikan.: ...  
67011  <|prompt|>Tulis ulang cerita sehingga memiliki...  
67012  <|prompt|>Sarankan langkah kebijakan baru untu...  
67013  <|prompt|>Kembangkan pernyataan tesis yang men...  
67015  <|prompt|>Cocokkan masukan berikut dengan jeni...  

[67017 rows x 4 columns]

Here we go.. There is the process which using Huge VRAM. We calculate perplexity of that dataset.  
So, it will create a column called "PPL" which calculate perplexity of the text of each rows in "QnA" column.

In [ ]:
%%time
df_MBZUAI['PPL'] = df_MBZUAI['QnA'].apply(Perplexity)
df_MBZUAI

In [ ]:
df_MBZUAI.to_csv("Eval-MBZUAI_Merak-7B-v1.csv")

## CITATION

Priyanka, M. 2022. "Perplexity of Language Models", (Online), (https://medium.com/@priyankads/perplexity-of-language-models-41160427ed72, accessed 8 August 2023).